<h1 align="center"> Intangible Intensity for S corps </h1> 

In this note we compute *Intangible Intensity* using  SOI data on business receipts and assets with price to sales valuations using compustat data

In [1]:
from IPython.display import HTML
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"
HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
<form action="javascript:code_toggle()"><input type="submit" value="Click here to toggle on/off the raw code."></form>''')

In [2]:
import pandas as pd
import numpy as np

import difflib as dl

from difflib import SequenceMatcher
from heapq import nlargest as _nlargest

pd.options.display.float_format = '{:,.2f}'.format

colnames=pd.read_csv('../RawData/IRS/colnames_soi_1120S.csv')
colnames.columns=[x.strip() for x in colnames.columns]
colnames.SOI1120S = colnames.SOI1120S.astype(int)
colnames.SOI1065 = colnames.SOI1065.astype(int)
colnames.CFC= colnames.CFC.astype(int)
colnames.CCANonCorporate= colnames.CCANonCorporate.astype(int)
colnames.CCACorporate= colnames.CCACorporate.astype(int)


In [3]:
def format_str(string):
    string=string.replace('[33]','')
    string=string.replace('[26]','')
    string=string.replace("[12]",'')
    string=string.replace('[34]','')
    string=string.replace(':','')
    string=string.strip()
    return string


def getBSData(soi_link):
    #soi_link= "https://www.irs.gov/pub/irs-soi/13co07s.xls"
    temp2=pd.read_excel(soi_link,skiprows=6)
    BSData=temp2.iloc[:,colnames.SOI1120S.values]
    BSData.index=[ format_str(str(x[0])) for x in temp2.iloc[:,[0]].values]
    BSData.columns=colnames.name.values
    BSData=BSData.iloc[:-1]
    return BSData

def get_close_matches_indexes(word, possibilities, n=3, cutoff=0.6):
    """Use SequenceMatcher to return a list of the indexes of the best 
    "good enough" matches. word is a sequence for which close matches 
    are desired (typically a string).
    possibilities is a list of sequences against which to match word
    (typically a list of strings).
    Optional arg n (default 3) is the maximum number of close matches to
    return.  n must be > 0.
    Optional arg cutoff (default 0.6) is a float in [0, 1].  Possibilities
    that don't score at least that similar to word are ignored.
    """

    if not n >  0:
        raise ValueError("n must be > 0: %r" % (n,))
    if not 0.0 <= cutoff <= 1.0:
        raise ValueError("cutoff must be in [0.0, 1.0]: %r" % (cutoff,))
    result = []
    s = SequenceMatcher()
    s.set_seq2(word)
    for idx, x in enumerate(possibilities):
        s.set_seq1(x)
        if s.real_quick_ratio() >= cutoff and \
           s.quick_ratio() >= cutoff and \
           s.ratio() >= cutoff:
            result.append((s.ratio(), idx))

    # Move the best scorers to head of list
    result = _nlargest(n, result)

    # Strip scores for the best n matches
    return [x for score, x in result]

## Years

In [4]:
years=['2007','2008','2009','2010','2011','2012','2013']
print(years)

['2007', '2008', '2009', '2010', '2011', '2012', '2013']


## Source of NIPA data 

In [5]:
fa_section3_link="http://users.cla.umn.edu/~erm/data/sr560/Data/RawData/BEA/FA/Section3all_xls.xlsx"
nipa_section6_link="http://users.cla.umn.edu/~erm/data/sr560/Data/RawData/BEA/NIPA/Section6all_xls.xlsx"

In [6]:
print(fa_section3_link)
print(nipa_section6_link)

http://users.cla.umn.edu/~erm/data/sr560/Data/RawData/BEA/FA/Section3all_xls.xlsx
http://users.cla.umn.edu/~erm/data/sr560/Data/RawData/BEA/NIPA/Section6all_xls.xlsx


## BEA FA:  CFC
Table 3.4ESI. Current-Cost Depreciation of Private Fixed Assets by Industry

In [7]:
CFC=pd.read_excel(fa_section3_link,sheet_name="FAAt304ESI-A",skiprows=7)
CFC['IndustryName']=CFC['Unnamed: 1']
CFC=CFC.drop(columns=['Unnamed: 1','Unnamed: 2'])
CFC=CFC[:-7]
CFC.Line=CFC.Line.astype(int)
CFC=CFC[CFC['Line'].isin(colnames.CFC.values)]
#CFC.iloc[get_close_matches_indexes('Management of companies and enterprise', CFC.IndustryName)[0],3:]=CFC[CFC.IndustryName==dl.get_close_matches('Administrative and support and waste', CFC.IndustryName)[0]].iloc[0,3:]+\
#CFC[CFC.IndustryName==dl.get_close_matches('Management of companies and enterprise', CFC.IndustryName)[0]].iloc[0,3:]
CFC.index=colnames.name
CFC=CFC.drop(CFC[CFC.IndustryName==dl.get_close_matches('Management of companies and enterprise', CFC.IndustryName)[0]].index)
CFC[years]

2007     2008     2009  \
name                                                                            
All                                                1,852.50 1,931.80 1,928.70   
Agriculture, forestry, fishing, and hunting           34.10    35.90    37.00   
Mining                                               112.60   125.40   118.70   
Utilities                                             58.70    64.80    67.20   
Construction                                          34.90    36.90    36.10   
Manufacturing                                        326.20   347.50   353.50   
Wholesale trade                                       55.10    56.10    55.40   
Retail trade                                          70.10    73.00    72.90   
Transportation and warehousing                        64.20    66.60    66.80   
Information                                          169.80   176.20   178.80   
Finance and insurance                                129.00   133.70   133.10   
Real estate and rental and leasing                   491.70   489.30   470.30   
Professional scientific\nand technical services       90.20    96.00    99.30   
Administrative and support and waste management...    28.10    29.00    29.80   
Educational services                                  17.60    19.00    20.60   
Health care and social assistance                     70.80    76.20    79.30   
Arts, entertainment, and recreation                   21.00    21.70    22.00   
Accommodation and food services                       28.40    30.30    30.70   
Other services                                        26.50    28.20    28.50   

                                                       2010     2011     2012  \
name                                                                            
All                                                1,933.80 1,997.30 2,082.40   
Agriculture, forestry, fishing, and hunting           37.60    39.60    42.20   
Mining                                               119.70   128.70   145.10   
Utilities                                             69.90    73.60    77.40   
Construction                                          34.00    34.10    35.50   
Manufacturing                                        356.70   369.30   383.40   
Wholesale trade                                       54.30    56.40    59.60   
Retail trade                                          71.40    74.30    78.20   
Transportation and warehousing                        65.90    67.50    70.30   
Information                                          185.10   197.50   206.50   
Finance and insurance                                130.70   133.50   138.50   
Real estate and rental and leasing                   462.10   462.30   469.60   
Professional scientific\nand technical services      102.50   106.00   109.30   
Administrative and support and waste management...    30.90    32.90    35.20   
Educational services                                  21.70    23.10    24.50   
Health care and social assistance                     81.30    85.30    89.50   
Arts, entertainment, and recreation                   21.90    22.10    22.40   
Accommodation and food services                       29.80    29.90    30.60   
Other services                                        28.30    29.20    30.20   

                                                       2013  
name                                                         
All                                                2,176.60  
Agriculture, forestry, fishing, and hunting           45.60  
Mining                                               151.40  
Utilities                                             80.00  
Construction                                          37.10  
Manufacturing                                        395.20  
Wholesale trade                                       61.30  
Retail trade                                          81.10  
Transportation and warehousing 

## BEA FA:  CAA (Noncorporate)
Table 6.13D. Noncorporate Capital Consumption Allowances by Industry

In [8]:
CCA_NonCorporate=pd.read_excel(nipa_section6_link,sheet_name="T61300D-A",skiprows=7)
CCA_NonCorporate['IndustryName']=CCA_NonCorporate['Unnamed: 1']
CCA_NonCorporate=CCA_NonCorporate.drop(columns=['Unnamed: 1','Unnamed: 2'])
CCA_NonCorporate=CCA_NonCorporate[:-4]
CCA_NonCorporate.Line=CCA_NonCorporate.Line.astype(int)
CCA_NonCorporate=CCA_NonCorporate[CCA_NonCorporate['Line'].isin(colnames.CCANonCorporate.values)]
CCA_NonCorporate.index=CFC.index
CCA_NonCorporate[years]/1000.0

2007   2008   2009  \
name                                                                      
All                                                313.09 386.18 381.62   
Agriculture, forestry, fishing, and hunting         17.85  18.97  18.92   
Mining                                              23.48  32.51  35.29   
Utilities                                            8.56  15.53  15.67   
Construction                                        10.58  10.78   8.53   
Manufacturing                                       27.67  42.93  38.65   
Wholesale trade                                      5.12   6.68   7.10   
Retail trade                                         7.11   8.39   7.95   
Transportation and warehousing                      12.28  15.63  17.59   
Information                                         34.45  42.12  43.66   
Finance and insurance                               11.51  13.51   9.88   
Real estate and rental and leasing                 108.70 125.21 125.89   
Professional scientific\nand technical services     12.17  13.80  13.33   
Administrative and support and waste management...   6.90   6.89   6.65   
Educational services                                 0.70   0.78   0.78   
Health care and social assistance                    8.66  10.61  10.32   
Arts, entertainment, and recreation                  4.81   5.74   5.39   
Accommodation and food services                     11.73  15.41  15.32   
Other services                                       0.81   0.68   0.71   

                                                     2010   2011   2012   2013  
name                                                                            
All                                                392.37 447.09 420.68 458.61  
Agriculture, forestry, fishing, and hunting         20.03  20.57  22.04  24.52  
Mining                                              38.71  47.59  48.43  57.33  
Utilities                                           16.15  23.13  21.41  25.03  
Construction                                         7.88   8.24   7.84   8.17  
Manufacturing                                       36.30  43.89  41.92  40.46  
Wholesale trade                                      7.18   9.19   8.76  10.61  
Retail trade                                         8.02   9.16   8.19   8.55  
Transportation and warehousing                      21.45  27.86  25.96  34.94  
Information                                         46.37  52.98  41.05  43.23  
Finance and insurance                               10.96  12.00  11.69  13.55  
Real estate and rental and leasing                 124.97 136.89 129.35 135.52  
Professional scientific\nand technical services     13.70  14.50  14.80  15.09  
Administrative and support and waste management...   7.57   7.47   7.43   8.13  
Educational services                                 0.72   0.80   0.80   0.98  
Health care and social assistance                   11.02  11.35   9.64   9.68  
Arts, entertainment, and recreation                  5.62   5.86   6.73   6.97  
Accommodation and food services                     14.89  15.10  13.94  15.07  
Other services                                       0.83   0.50   0.67   0.76

## BEA FA:  CAA (Corporate)
Table 6.22D. Corporate Capital Consumption Allowances by Industry

In [9]:
CCA_Corporate=pd.read_excel(nipa_section6_link,sheet_name="T62200D-A",skiprows=7)
CCA_Corporate['IndustryName']=CCA_Corporate['Unnamed: 1']
CCA_Corporate=CCA_Corporate.drop(columns=['Unnamed: 1','Unnamed: 2'])
CCA_Corporate=CCA_Corporate[:-7]
CCA_Corporate.Line=CCA_Corporate.Line.astype(int)
CCA_Corporate.index=CCA_Corporate.Line
CCA_Corporate=CCA_Corporate[CCA_Corporate['Line'].isin(colnames.CCACorporate.values)]
#CCA_Corporate.iloc[get_close_matches_indexes('Management of companies and enterprise', CCA_Corporate.IndustryName)[0],3:]=CCA_Corporate[CCA_Corporate.IndustryName==dl.get_close_matches('Administrative and support and waste', CCA_Corporate.IndustryName)[0]].iloc[0,3:]+\
#CCA_Corporate[CCA_Corporate.IndustryName==dl.get_close_matches('Management of companies and enterprise', CCA_Corporate.IndustryName)[0]].iloc[0,3:]
CCA_Corporate.index=colnames.name
CCA_Corporate=CCA_Corporate.drop(CCA_Corporate[CCA_Corporate.IndustryName==dl.get_close_matches('Management of companies and enterprise', CCA_Corporate.IndustryName)[0]].index)
CCA_Corporate[years]/1000.0

2007     2008     2009  \
name                                                                            
All                                                1,013.76 1,197.95 1,180.49   
Agriculture, forestry, fishing, and hunting            7.62     9.66     9.38   
Mining                                                29.05    43.27    44.67   
Utilities                                             42.61    60.09    73.98   
Construction                                          25.17    28.14    22.97   
Manufacturing                                        369.20   410.98   412.04   
Wholesale trade                                       75.54    93.88    89.30   
Retail trade                                          52.27    68.25    61.66   
Transportation and warehousing                        50.57    57.57    55.26   
Information                                          118.36   139.95   137.63   
Finance and insurance                                 64.88    72.24    68.14   
Real estate and rental and leasing                    41.72    49.37    44.45   
Professional scientific\nand technical services       38.33    44.47    46.03   
Administrative and support and waste management...    12.41    14.78    14.34   
Educational services                                   0.85     1.20     1.69   
Health care and social assistance                     10.69    13.62    12.29   
Arts, entertainment, and recreation                    4.67     5.68     5.60   
Accommodation and food services                       17.43    22.17    21.55   
Other services                                         5.58     6.18     5.41   

                                                       2010     2011     2012  \
name                                                                            
All                                                1,213.48 1,384.17 1,245.21   
Agriculture, forestry, fishing, and hunting           10.62    12.08    10.96   
Mining                                                44.73    62.87    61.70   
Utilities                                             80.56    98.90    92.77   
Construction                                          20.64    22.72    18.71   
Manufacturing                                        417.75   470.19   439.29   
Wholesale trade                                       97.07   112.28    99.65   
Retail trade                                          66.26    73.34    60.72   
Transportation and warehousing                        57.91    70.47    59.60   
Information                                          138.52   149.65   129.31   
Finance and insurance                                 69.40    74.43    68.87   
Real estate and rental and leasing                    44.67    55.44    45.82   
Professional scientific\nand technical services       47.75    52.56    48.61   
Administrative and support and waste management...    15.04    16.84    14.86   
Educational services                                   1.80     2.21     1.59   
Health care and social assistance                     12.89    15.38    11.28   
Arts, entertainment, and recreation                    6.45     6.93     6.24   
Accommodation and food services                       21.34    22.36    19.73   
Other services                                         4.97     5.75     4.94   

                                                       2013  
name                                                         
All                                                1,294.97  
Agriculture, forestry, fishing, and hunting           11.62  
Mining                                                62.14  
Utilities                                             83.50  
Construction                                          21.08  
Manufacturing                                        460.50  
Wholesale trade                                      107.65  
Retail trade                                          63.76  
Transportation and warehousing 

## Index for converting CCA to CFC 

Tax depreciation to economic depreciation using 
$$ \frac {\text{CFC}}   { \text{CCA ( Noncorporate) + CCA ( Corporate)}} $$

In [10]:
IndexDep=CFC[years]/(CCA_NonCorporate[years]/1000.0+CCA_Corporate[years]/1000.0)
display(IndexDep)

2007  2008  2009  2010  \
name                                                                         
All                                                 1.40  1.22  1.23  1.20   
Agriculture, forestry, fishing, and hunting         1.34  1.25  1.31  1.23   
Mining                                              2.14  1.65  1.48  1.43   
Utilities                                           1.15  0.86  0.75  0.72   
Construction                                        0.98  0.95  1.15  1.19   
Manufacturing                                       0.82  0.77  0.78  0.79   
Wholesale trade                                     0.68  0.56  0.57  0.52   
Retail trade                                        1.18  0.95  1.05  0.96   
Transportation and warehousing                      1.02  0.91  0.92  0.83   
Information                                         1.11  0.97  0.99  1.00   
Finance and insurance                               1.69  1.56  1.71  1.63   
Real estate and rental and leasing                  3.27  2.80  2.76  2.72   
Professional scientific\nand technical services     1.79  1.65  1.67  1.67   
Administrative and support and waste management...  1.46  1.34  1.42  1.37   
Educational services                               11.30  9.59  8.33  8.60   
Health care and social assistance                   3.66  3.15  3.51  3.40   
Arts, entertainment, and recreation                 2.21  1.90  2.00  1.81   
Accommodation and food services                     0.97  0.81  0.83  0.82   
Other services                                      4.15  4.11  4.66  4.88   

                                                    2011  2012  2013  
name                                                                  
All                                                 1.09  1.25  1.24  
Agriculture, forestry, fishing, and hunting         1.21  1.28  1.26  
Mining                                              1.17  1.32  1.27  
Utilities                                           0.60  0.68  0.74  
Construction                                        1.10  1.34  1.27  
Manufacturing                                       0.72  0.80  0.79  
Wholesale trade                                     0.46  0.55  0.52  
Retail trade                                        0.90  1.13  1.12  
Transportation and warehousing                      0.69  0.82  0.76  
Information                                         0.97  1.21  1.22  
Finance and insurance                               1.54  1.72  1.58  
Real estate and rental and leasing                  2.40  2.68  2.72  
Professional scientific\nand technical services     1.58  1.72  1.71  
Administrative and support and waste management...  1.35  1.58  1.63  
Educational services                                7.67 10.25 10.77  
Health care and social assistance                   3.19  4.28  4.27  
Arts, entertainment, and recreation                 1.73  1.73  1.75  
Accommodation and food services                     0.80  0.91  0.92  
Other services                                      4.67  5.38  5.24

## BEA FA:  Current Cost FA
Table 3.1ESI. Current-Cost Net Stock of Private Fixed Assets by Industry

In [11]:
CCNFA=pd.read_excel(fa_section3_link,sheet_name="FAAt301ESI-A",skiprows=7)
CCNFA['IndustryName']=CCNFA['Unnamed: 1']
CCNFA=CCNFA.iloc[:-7]
CCNFA.Line=CCNFA.Line.astype(int)
CCNFA.index=CCNFA.Line
CCNFA=CCNFA[CCNFA['Line'].isin(colnames.CCNFA.values)]
#CCNFA.iloc[get_close_matches_indexes('Management of companies and enterprise', CCNFA.IndustryName)[0],3:]=CCNFA[CCNFA.IndustryName==dl.get_close_matches('Administrative and support and waste', CCNFA.IndustryName)[0]].iloc[0,3:]+\
#CCNFA[CCNFA.IndustryName==dl.get_close_matches('Management of companies and enterprise', CCNFA.IndustryName)[0]].iloc[0,3:]
CCNFA.index=colnames.name
CCNFA=CCNFA.drop(CCNFA[CCNFA.IndustryName==dl.get_close_matches('Management of companies and enterprise', CCNFA.IndustryName)[0]].index)
CCNFA[years]


2007      2008  \
name                                                                     
All                                                34,154.60 34,981.30   
Agriculture, forestry, fishing, and hunting           472.70    492.10   
Mining                                              1,512.50  1,648.90   
Utilities                                           1,590.60  1,745.00   
Construction                                          264.90    284.00   
Manufacturing                                       3,009.10  3,199.90   
Wholesale trade                                       480.40    507.10   
Retail trade                                        1,107.10  1,183.60   
Transportation and warehousing                      1,036.80  1,098.40   
Information                                         1,656.30  1,722.20   
Finance and insurance                               1,164.20  1,215.90   
Real estate and rental and leasing                 17,842.60 17,613.70   
Professional scientific\nand technical services       512.30    549.40   
Administrative and support and waste management...    230.40    238.40   
Educational services                                  398.80    448.50   
Health care and social assistance                   1,160.90  1,220.60   
Arts, entertainment, and recreation                   280.30    293.40   
Accommodation and food services                       529.20    569.00   
Other services                                        561.60    583.80   

                                                        2009      2010  \
name                                                                     
All                                                34,101.10 34,582.20   
Agriculture, forestry, fishing, and hunting           479.70    487.10   
Mining                                              1,491.20  1,574.50   
Utilities                                           1,736.10  1,859.30   
Construction                                          267.00    263.60   
Manufacturing                                       3,160.10  3,214.90   
Wholesale trade                                       487.50    491.20   
Retail trade                                        1,127.50  1,131.80   
Transportation and warehousing                      1,072.50  1,095.20   
Information                                         1,722.90  1,829.80   
Finance and insurance                               1,161.30  1,153.80   
Real estate and rental and leasing                 17,200.50 17,227.40   
Professional scientific\nand technical services       557.40    576.30   
Administrative and support and waste management...    237.90    244.60   
Educational services                                  455.30    469.20   
Health care and social assistance                   1,195.50  1,220.70   
Arts, entertainment, and recreation                   287.60    289.10   
Accommodation and food services                       548.00    541.90   
Other services                                        557.50    557.30   

                                                        2011      2012  \
name                                                                     
All                                                35,557.70 36,693.10   
Agriculture, forestry, fishing, and hunting           507.70    536.50   
Mining                                              1,752.10  1,886.40   
Utilities                                           1,980.40  2,064.60   
Construction                                          271.10    278.60   
Manufacturing                                       3,340.20  3,438.90   
Wholesale trade                                       515.30    533.70   
Retail trade                                        1,177.20  1,205.60   
Transportation and warehousing                      1,136.40  1,170.20   
Information                                         1,908.30  1,948.40   
Finance and insurance                               1,183.

## BEA FA:  Historical Cost FA
Table 3.3ESI. Historical-Cost Net Stock of Private Fixed Assets by Industry

In [12]:
HCNFA=pd.read_excel(fa_section3_link,sheet_name="FAAt303ESI-A",skiprows=7)
HCNFA['IndustryName']=HCNFA['Unnamed: 1']
HCNFA=HCNFA.iloc[:-7]
HCNFA.Line=HCNFA.Line.astype(int)
HCNFA.index=HCNFA.Line
HCNFA=HCNFA[HCNFA['Line'].isin(colnames.HCNFA.values)]
#HCNFA.iloc[get_close_matches_indexes('Management of companies and enterprise', HCNFA.IndustryName)[0],3:]=HCNFA[HCNFA.IndustryName==dl.get_close_matches('Administrative and support and waste', HCNFA.IndustryName)[0]].iloc[0,3:]+\
#HCNFA[HCNFA.IndustryName==dl.get_close_matches('Management of companies and enterprise', HCNFA.IndustryName)[0]].iloc[0,3:]
HCNFA.index=colnames.name
HCNFA=HCNFA.drop(HCNFA[HCNFA.IndustryName==dl.get_close_matches('Management of companies and enterprise', HCNFA.IndustryName)[0]].index)

HCNFA[years]

2007      2008  \
name                                                                     
All                                                20,120.40 21,021.30   
Agriculture, forestry, fishing, and hunting           264.80    280.20   
Mining                                                662.90    764.40   
Utilities                                             854.90    917.00   
Construction                                          215.20    228.20   
Manufacturing                                       2,179.00  2,295.20   
Wholesale trade                                       367.00    376.90   
Retail trade                                          697.10    722.40   
Transportation and warehousing                        591.00    619.50   
Information                                         1,422.80  1,482.30   
Finance and insurance                                 859.90    876.80   
Real estate and rental and leasing                  9,411.50  9,691.60   
Professional scientific\nand technical services       434.70    462.10   
Administrative and support and waste management...    171.30    174.00   
Educational services                                  233.20    251.30   
Health care and social assistance                     755.20    810.80   
Arts, entertainment, and recreation                   191.80    203.00   
Accommodation and food services                       322.60    355.90   
Other services                                        308.50    324.20   

                                                        2009      2010  \
name                                                                     
All                                                21,458.90 21,923.20   
Agriculture, forestry, fishing, and hunting           293.30    307.00   
Mining                                                813.20    876.00   
Utilities                                             979.90  1,031.30   
Construction                                          216.20    213.10   
Manufacturing                                       2,341.30  2,390.50   
Wholesale trade                                       374.10    378.30   
Retail trade                                          726.20    735.00   
Transportation and warehousing                        626.70    639.90   
Information                                         1,517.80  1,575.40   
Finance and insurance                                 864.10    862.00   
Real estate and rental and leasing                  9,809.00  9,927.20   
Professional scientific\nand technical services       481.00    497.50   
Administrative and support and waste management...    181.10    187.10   
Educational services                                  267.80    280.80   
Health care and social assistance                     855.70    895.00   
Arts, entertainment, and recreation                   213.20    218.50   
Accommodation and food services                       372.10    373.20   
Other services                                        334.20    340.80   

                                                        2011      2012  \
name                                                                     
All                                                22,519.00 23,282.20   
Agriculture, forestry, fishing, and hunting           324.80    351.90   
Mining                                                974.70  1,098.50   
Utilities                                           1,088.50  1,161.80   
Construction                                          214.90    220.10   
Manufacturing                                       2,472.30  2,571.10   
Wholesale trade                                       392.50    408.10   
Retail trade                                          752.40    770.80   
Transportation and warehousing                        659.50    690.60   
Information                                         1,633.30  1,680.70   
Finance and insurance                                 870.

## BEA FA:  Historical Cost Depreciation
Table 3.6ESI. Historical-Cost Depreciation of Private Fixed Assets by Industry

In [13]:
HFC=pd.read_excel(fa_section3_link,sheet_name="FAAt306ESI-A",skiprows=7)
HFC['IndustryName']=HFC['Unnamed: 1']
HFC=HFC.iloc[:-7]
HFC.Line=HFC.Line.astype(int)
HFC.index=HFC.Line
HFC=HFC[HFC['Line'].isin(colnames.HFC.values)]
#HFC.iloc[get_close_matches_indexes('Management of companies and enterprise', HFC.IndustryName)[0],3:]=HFC[HFC.IndustryName==dl.get_close_matches('Administrative and support and waste', HFC.IndustryName)[0]].iloc[0,3:]+\
#HFC[HFC.IndustryName==dl.get_close_matches('Management of companies and enterprise', HFC.IndustryName)[0]].iloc[0,3:]
HFC.index=colnames.name
HFC=HFC.drop(HFC[HFC.IndustryName==dl.get_close_matches('Management of companies and enterprise', HFC.IndustryName)[0]].index)
HFC[years]

2007     2008     2009  \
name                                                                            
All                                                1,507.80 1,578.80 1,616.70   
Agriculture, forestry, fishing, and hunting           26.40    27.60    28.80   
Mining                                                51.20    59.10    64.90   
Utilities                                             40.70    43.90    47.20   
Construction                                          32.30    34.00    32.90   
Manufacturing                                        284.90   301.20   311.70   
Wholesale trade                                       52.60    52.60    51.90   
Retail trade                                          59.40    60.90    60.70   
Transportation and warehousing                        51.10    52.50    52.80   
Information                                          172.00   179.40   184.60   
Finance and insurance                                124.50   128.10   127.10   
Real estate and rental and leasing                   338.30   347.40   346.50   
Professional scientific\nand technical services       89.20    94.20    98.50   
Administrative and support and waste management...    27.10    27.60    28.50   
Educational services                                  14.70    15.80    17.10   
Health care and social assistance                     64.20    69.30    73.40   
Arts, entertainment, and recreation                   17.10    17.90    18.50   
Accommodation and food services                       21.70    23.10    24.00   
Other services                                        20.80    22.20    22.90   

                                                       2010     2011     2012  \
name                                                                            
All                                                1,639.50 1,683.90 1,752.00   
Agriculture, forestry, fishing, and hunting           30.10    31.80    34.40   
Mining                                                69.20    76.00    86.00   
Utilities                                             49.50    51.40    54.20   
Construction                                          31.10    30.80    31.60   
Manufacturing                                        315.70   323.80   335.80   
Wholesale trade                                       51.20    52.60    55.30   
Retail trade                                          60.50    62.40    65.50   
Transportation and warehousing                        52.30    53.20    55.30   
Information                                          191.50   201.60   210.90   
Finance and insurance                                125.50   126.10   130.30   
Real estate and rental and leasing                   344.00   344.10   348.30   
Professional scientific\nand technical services      101.70   103.90   106.50   
Administrative and support and waste management...    30.00    31.60    33.70   
Educational services                                  18.30    19.50    20.70   
Health care and social assistance                     76.70    80.40    84.70   
Arts, entertainment, and recreation                   18.90    19.20    19.50   
Accommodation and food services                       24.00    24.00    24.50   
Other services                                        23.30    23.90    24.70   

                                                       2013  
name                                                         
All                                                1,833.50  
Agriculture, forestry, fishing, and hunting           37.80  
Mining                                                96.40  
Utilities                                             57.10  
Construction                                          33.30  
Manufacturing                                        349.10  
Wholesale trade                                       57.00  
Retail trade                                          68.10  
Transportation and warehousing 

## BEA FA:  Current Cost Depreciation
Table 3.4ESI. Current-Cost Depreciation of Private Fixed Assets by Industry

In [14]:
CFC=pd.read_excel(fa_section3_link,sheet_name="FAAt304ESI-A",skiprows=7)
CFC['IndustryName']=CFC['Unnamed: 1']
CFC=CFC.drop(columns=['Unnamed: 1','Unnamed: 2'])
CFC=CFC[:-7]
CFC.Line=CFC.Line.astype(int)
CFC=CFC[CFC['Line'].isin(colnames.CFC.values)]
#CFC.iloc[get_close_matches_indexes('Management of companies and enterprise', CFC.IndustryName)[0],3:]=CFC[CFC.IndustryName==dl.get_close_matches('Administrative and support and waste', CFC.IndustryName)[0]].iloc[0,3:]+\
#CFC[CFC.IndustryName==dl.get_close_matches('Management of companies and enterprise', CFC.IndustryName)[0]].iloc[0,3:]
CFC.index=colnames.name
CFC=CFC.drop(CFC[CFC.IndustryName==dl.get_close_matches('Management of companies and enterprise', CFC.IndustryName)[0]].index)
CFC[years]

2007     2008     2009  \
name                                                                            
All                                                1,852.50 1,931.80 1,928.70   
Agriculture, forestry, fishing, and hunting           34.10    35.90    37.00   
Mining                                               112.60   125.40   118.70   
Utilities                                             58.70    64.80    67.20   
Construction                                          34.90    36.90    36.10   
Manufacturing                                        326.20   347.50   353.50   
Wholesale trade                                       55.10    56.10    55.40   
Retail trade                                          70.10    73.00    72.90   
Transportation and warehousing                        64.20    66.60    66.80   
Information                                          169.80   176.20   178.80   
Finance and insurance                                129.00   133.70   133.10   
Real estate and rental and leasing                   491.70   489.30   470.30   
Professional scientific\nand technical services       90.20    96.00    99.30   
Administrative and support and waste management...    28.10    29.00    29.80   
Educational services                                  17.60    19.00    20.60   
Health care and social assistance                     70.80    76.20    79.30   
Arts, entertainment, and recreation                   21.00    21.70    22.00   
Accommodation and food services                       28.40    30.30    30.70   
Other services                                        26.50    28.20    28.50   

                                                       2010     2011     2012  \
name                                                                            
All                                                1,933.80 1,997.30 2,082.40   
Agriculture, forestry, fishing, and hunting           37.60    39.60    42.20   
Mining                                               119.70   128.70   145.10   
Utilities                                             69.90    73.60    77.40   
Construction                                          34.00    34.10    35.50   
Manufacturing                                        356.70   369.30   383.40   
Wholesale trade                                       54.30    56.40    59.60   
Retail trade                                          71.40    74.30    78.20   
Transportation and warehousing                        65.90    67.50    70.30   
Information                                          185.10   197.50   206.50   
Finance and insurance                                130.70   133.50   138.50   
Real estate and rental and leasing                   462.10   462.30   469.60   
Professional scientific\nand technical services      102.50   106.00   109.30   
Administrative and support and waste management...    30.90    32.90    35.20   
Educational services                                  21.70    23.10    24.50   
Health care and social assistance                     81.30    85.30    89.50   
Arts, entertainment, and recreation                   21.90    22.10    22.40   
Accommodation and food services                       29.80    29.90    30.60   
Other services                                        28.30    29.20    30.20   

                                                       2013  
name                                                         
All                                                2,176.60  
Agriculture, forestry, fishing, and hunting           45.60  
Mining                                               151.40  
Utilities                                             80.00  
Construction                                          37.10  
Manufacturing                                        395.20  
Wholesale trade                                       61.30  
Retail trade                                          81.10  
Transportation and warehousing 

## Index for Historical Cost to Current Cost for Gross Fixed Assets 

$$ \frac{\text{HCNFA}+ \text{HFC} } {{\text{CCNFA}+ \text{CFC} } } $$

In [15]:
HCGFA=HCNFA+HFC
CCGFA=CCNFA+CFC
IndexCCFA=pd.DataFrame(CCGFA[years]/HCGFA[years])
display(IndexCCFA)
IndexCCFA['IndustryName']=CCNFA.IndustryName
IndexCCFA['IndustryName'].iloc[0]='All'
IndexCCFA['IndustryName'].iloc[-1]='Other services'

2007  2008  2009  2010  \
name                                                                         
All                                                 1.66  1.63  1.56  1.55   
Agriculture, forestry, fishing, and hunting         1.74  1.72  1.60  1.56   
Mining                                              2.28  2.15  1.83  1.79   
Utilities                                           1.84  1.88  1.76  1.78   
Construction                                        1.21  1.22  1.22  1.22   
Manufacturing                                       1.35  1.37  1.32  1.32   
Wholesale trade                                     1.28  1.31  1.27  1.27   
Retail trade                                        1.56  1.60  1.53  1.51   
Transportation and warehousing                      1.71  1.73  1.68  1.68   
Information                                         1.15  1.14  1.12  1.14   
Finance and insurance                               1.31  1.34  1.31  1.30   
Real estate and rental and leasing                  1.88  1.80  1.74  1.72   
Professional scientific\nand technical services     1.15  1.16  1.13  1.13   
Administrative and support and waste management...  1.30  1.33  1.28  1.27   
Educational services                                1.68  1.75  1.67  1.64   
Health care and social assistance                   1.50  1.47  1.37  1.34   
Arts, entertainment, and recreation                 1.44  1.43  1.34  1.31   
Accommodation and food services                     1.62  1.58  1.46  1.44   
Other services                                      1.79  1.77  1.64  1.61   

                                                    2011  2012  2013  
name                                                                  
All                                                 1.55  1.55  1.57  
Agriculture, forestry, fishing, and hunting         1.53  1.50  1.48  
Mining                                              1.79  1.72  1.68  
Utilities                                           1.80  1.76  1.72  
Construction                                        1.24  1.25  1.23  
Manufacturing                                       1.33  1.31  1.31  
Wholesale trade                                     1.28  1.28  1.28  
Retail trade                                        1.54  1.54  1.54  
Transportation and warehousing                      1.69  1.66  1.63  
Information                                         1.15  1.14  1.13  
Finance and insurance                               1.32  1.32  1.32  
Real estate and rental and leasing                  1.72  1.73  1.80  
Professional scientific\nand technical services     1.15  1.14  1.15  
Administrative and support and waste management...  1.28  1.28  1.27  
Educational services                                1.66  1.64  1.65  
Health care and social assistance                   1.33  1.32  1.33  
Arts, entertainment, and recreation                 1.31  1.31  1.33  
Accommodation and food services                     1.45  1.45  1.48  
Other services                                      1.62  1.62  1.66

C:\Users\admin\Anaconda3\lib\site-packages\pandas\core\indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)


## Source SOI Data
 From the SOI data we extract business receipts and define total tangible assets using


In [16]:

def downloadSCorpData(year):
    if int(year) > 2005:
        soi_link= "https://www.irs.gov/pub/irs-soi/"+ year[2:] + "co07s.xls"
    elif int(year)==2005:
        soi_link="https://www.irs.gov/pub/irs-soi/05co1120s07.xls"
    elif int(year)==2004:
        soi_link="https://www.irs.gov/pub/irs-soi/04co14ccr.xls"
    elif int(year)==2003:
        soi_link="https://www.irs.gov/pub/irs-soi/03co14bs.xls"
    elif int(year)==2002:
        soi_link="https://www.irs.gov/pub/irs-soi/02co14bs.xls"
    elif int(year)==2001:
        soi_link="https://www.irs.gov/pub/irs-soi/01co14bs.xls"
    elif int(year)==2000:
        soi_link="https://www.irs.gov/pub/irs-soi/00co14bs.xls"
    elif int(year)==1999:
        soi_link="https://www.irs.gov/pub/irs-soi/99co14bs.xls"
    elif int(year)==1998:
        soi_link="https://www.irs.gov/pub/irs-soi/98co14bs.xls"
            
    print(soi_link)
    ScorpData=getBSData(soi_link)
    ScorpData=ScorpData.T
  #  ScorpData.iloc[get_close_matches_indexes('Management of companies and enterprise', ScorpData.index)[0],7:]=ScorpData.iloc[get_close_matches_indexes('Management of companies and enterprise', ScorpData.index)[0],7:]+ScorpData.iloc[get_close_matches_indexes('Administrative and support and waste', ScorpData.index)[0],7:]
    ScorpData=ScorpData.drop(ScorpData[ScorpData.index==dl.get_close_matches('Management of companies and enterprise', ScorpData.index)[0]].index)
    return ScorpData

def addHCFA(ScorpData):
    CCFASOI=[]
    ScorpData['HCFA']=ScorpData[dl.get_close_matches('Depreciable assets', ScorpData.columns)[0]]+\
    ScorpData[dl.get_close_matches('Depletable assets', ScorpData.columns)[0]]
    return ScorpData

def addCCFA(ScorpData,year):
    CCFASOI=[]
    for SOIindex in ScorpData.index:
        factor=IndexCCFA.iloc[get_close_matches_indexes(SOIindex,IndexCCFA.index)][year].values
        HCFASOI=ScorpData['HCFA'][SOIindex] 
        HCFASOI=float(HCFASOI)
        factor=float(factor[0])
        CCFASOI.append(HCFASOI*factor)

    ScorpData['CCFA']=  np.array(CCFASOI)

    return ScorpData

def addCCA(ScorpData):
    ScorpData['CCA']=ScorpData[dl.get_close_matches('Less: Accumulated depreciation', ScorpData.columns)[0]]+\
    ScorpData[dl.get_close_matches('Less: Accumulated depletion', ScorpData.columns)[0]]
    return ScorpData

def addCFC(ScorpData,year):
    CFCSOI=[]

    factorAll=IndexDep.iloc[get_close_matches_indexes('All',IndexDep.index)][year].values    
        
    for SOIindex in ScorpData.index:
        if len(get_close_matches_indexes(SOIindex,IndexDep.index))>0:
            factor=IndexDep.iloc[get_close_matches_indexes(SOIindex,IndexDep.index)][year].values
        else:
            factor=factorAll    
    
        if factor[0]>3.0:
            factor=factorAll
       
        CCASOI=ScorpData['CCA'][SOIindex] 
        CCASOI=float(CCASOI)
        factor=float(factor[0])
        CFCSOI.append(CCASOI*factor)
            

    ScorpData['CFC']=  np.array(CFCSOI)
    return ScorpData


def addTotalTangibleAssets(ScorpData):
    ScorpData['CurrentAssets']= ScorpData[dl.get_close_matches('Notes and accounts receivable', ScorpData.columns)[0]]\
                           - ScorpData[dl.get_close_matches('Less: Allowance for bad debts..', ScorpData.columns)[0]] \
                           +  ScorpData[dl.get_close_matches('other assets', ScorpData.columns)[0]] 
    
    ScorpData['Inventories']= ScorpData[dl.get_close_matches('Inventories', ScorpData.columns)[0]] 
    
    ScorpData['FixedAssetsLessDep']= ScorpData[dl.get_close_matches('CCFA', ScorpData.columns)[0]] \
                           - ScorpData[dl.get_close_matches('CFC', ScorpData.columns)[0]] \
                           
    ScorpData['Land']= ScorpData[dl.get_close_matches('Land', ScorpData.columns)[0]] 
    
    ScorpData['CurrentLiabilities']= ScorpData[dl.get_close_matches('Accounts payable..', ScorpData.columns)[0]] \
                            + ScorpData[dl.get_close_matches('Other current liabilities..', ScorpData.columns)[0]] 
    
    ScorpData['TotalTangibleAssets']= ScorpData[dl.get_close_matches('Notes and accounts receivable', ScorpData.columns)[0]]\
                           - ScorpData[dl.get_close_matches('Less: Allowance for bad debts..', ScorpData.columns)[0]] \
                           + ScorpData[dl.get_close_matches('Inventories', ScorpData.columns)[0]] \
                           + ScorpData[dl.get_close_matches('other current assets', ScorpData.columns)[0]] \
                           + ScorpData[dl.get_close_matches('CCFA', ScorpData.columns)[0]] \
                           - ScorpData[dl.get_close_matches('CFC', ScorpData.columns)[0]] \
                           + ScorpData[dl.get_close_matches('Land', ScorpData.columns)[0]] \
                           + ScorpData[dl.get_close_matches('other assets', ScorpData.columns)[0]]\
        

    ScorpData['TotalTangibleAssets']= ScorpData['TotalTangibleAssets']+\
                           - ScorpData[dl.get_close_matches('Accounts payable..', ScorpData.columns)[0]] \
                           - ScorpData[dl.get_close_matches('Other current liabilities..', ScorpData.columns)[0]] \

    ScorpData['TotalTangibleAssetsMrtg'] = ScorpData['TotalTangibleAssets']+ \
                                     + ScorpData[dl.get_close_matches('Mortgage and real estate loans..', ScorpData.columns)[0]]\
                                     - ScorpData[dl.get_close_matches('Mortgages, notes, bonds, one year or more', ScorpData.columns)[0]] 

    ScorpData['BusinessReceipts'] = ScorpData[dl.get_close_matches('Business receipts', ScorpData.columns)[0]]
    return ScorpData

    
    


def getSCropData(year):
    ScorpData =  downloadSCorpData(year)
    ScorpData = addHCFA (ScorpData )
    ScorpData = addCCFA (ScorpData,year)
    ScorpData = addCCA (ScorpData )
    ScorpData = addCFC (ScorpData,year )
    ScorpData = addTotalTangibleAssets (ScorpData)
    return ScorpData

def getPriceSalesMultiples():
    price_sales_multiple=pd.read_csv('price_sales_mean.csv')
    price_sales_multiple.columns=['IndustryName','PSMultiple']
    price_sales_multiple['IndustryName'].iloc[1]='Mining'
    price_sales_multiple['IndustryName'].iloc[12]='Administrative and support and waste management and remediation services'
    return price_sales_multiple

def getIntanIntensity(ScorpData,price_sales_multiple,liquidity_factor):
    IITaxdata=pd.DataFrame( ScorpData['BusinessReceipts']/ScorpData['TotalTangibleAssets'],columns=['Sales_TangibleAssets'])
    price_sales_multiple = getPriceSalesMultiples()
    Value_Sales=[]

    factorAll=IndexDep.iloc[get_close_matches_indexes('All',price_sales_multiple.IndustryName)].values    
        
    for IITaxdataindex in IITaxdata.index:
        if len(get_close_matches_indexes(IITaxdataindex,price_sales_multiple.IndustryName))>0:
            factor=price_sales_multiple.iloc[get_close_matches_indexes(IITaxdataindex,price_sales_multiple.IndustryName)].PSMultiple.values    
        else:
            factor=factorAll    
       
        Value_Sales.append(factor[0])
            

    IITaxdata['Value_Sales']=  np.array(Value_Sales)
    IITaxdata['Value_Sales_alt']=  np.array(Value_Sales)*liquidity_factor

    IITaxdata['Value_TangibleAssets']=IITaxdata['Sales_TangibleAssets']*IITaxdata['Value_Sales']
    IITaxdata['Intan_TangibleAssets']=IITaxdata['Value_TangibleAssets']-1.0
    IITaxdata['IntanIntensity']=IITaxdata['Intan_TangibleAssets']/IITaxdata['Value_TangibleAssets']
    IITaxdata['Value_TangibleAssets_alt']=IITaxdata['Sales_TangibleAssets']*IITaxdata['Value_Sales_alt']
    IITaxdata['Intan_TangibleAssets_alt']=IITaxdata['Value_TangibleAssets_alt']-1.0
    IITaxdata['IntanIntensity_alt']=IITaxdata['Intan_TangibleAssets_alt']/IITaxdata['Value_TangibleAssets_alt']
    IITaxdata['IntanIntensityMrtg']= 1- (ScorpData['TotalTangibleAssetsMrtg']/ScorpData['BusinessReceipts'])/IITaxdata['Value_Sales']


    return IITaxdata[['IntanIntensity','IntanIntensity_alt','Sales_TangibleAssets','Value_Sales','IntanIntensityMrtg']]
    


In [17]:

IITaxdataList=[]
IITaxdata_altList=[]
IITaxdataMrtgList=[]
MktCapToSalesList=[]
BusReceiptsToTangibleAssetsList=[]
    
for year in years:
    ScorpData =getSCropData (year)  
    price_sales_multiple = getPriceSalesMultiples()
    liquidity_factor =0.75
    temp=[]
    temp = getIntanIntensity(ScorpData,price_sales_multiple,liquidity_factor)
    IITaxdataList.append(temp.IntanIntensity.values  )
    IITaxdata_altList.append(temp.IntanIntensity_alt.values)
    MktCapToSalesList.append(temp.Value_Sales.values)
    BusReceiptsToTangibleAssetsList.append(temp.Sales_TangibleAssets.values)
    IITaxdataMrtgList.append(temp.IntanIntensityMrtg.values)

IITaxdata = pd.DataFrame(IITaxdataList,index=years,columns=temp.index).T
IITaxdataAlt = pd.DataFrame(IITaxdata_altList,index=years,columns=temp.index).T
MktCapToSales = pd.DataFrame(MktCapToSalesList,index=years,columns=temp.index).T
BusReceiptsToTangibleAssets = pd.DataFrame(BusReceiptsToTangibleAssetsList,index=years,columns=temp.index).T
IITaxdataMrtg =  pd.DataFrame(IITaxdataMrtgList,index=years,columns=temp.index).T
 #   IITaxdataList.append(IITaxdata)
 #   IITaxdata_altList.append(IITaxdata_alt)
    
    

#IITaxdata = pd.DataFrame(IITaxdataList,index=years).T
#IITaxdataAlt = pd.DataFrame(IITaxdata_altList,index=years).T



https://www.irs.gov/pub/irs-soi/07co07s.xls
https://www.irs.gov/pub/irs-soi/08co07s.xls
https://www.irs.gov/pub/irs-soi/09co07s.xls
https://www.irs.gov/pub/irs-soi/10co07s.xls
https://www.irs.gov/pub/irs-soi/11co07s.xls
https://www.irs.gov/pub/irs-soi/12co07s.xls
https://www.irs.gov/pub/irs-soi/13co07s.xls


## Total Tangible Assets SOI
$$\text{TotalTangibleAssets} = \text{Accounts receivable net of bad debts and  payables} + \text{inventories} +\text{other current assets net of current liabilities} + \text{Fixed assets (current cost) net of depreciation} + \text{land} + \text{other assets}    $$


In [18]:
#ScorpData[['BusinessReceipts','TotalTangibleAssets']]/1000.0

## Tangible Assets (SOI) divided by Business Receipts (SOI)
$$ \frac{ \text{TotalTangibleAssets (SOI)  }  } {\text{Business Receipts (SOI) } } $$

In [19]:

display(1/BusReceiptsToTangibleAssets)


2007  2008  2009  2010  \
All                                                 0.32  0.34  0.34  0.33   
Agriculture, forestry, fishing, and hunting         0.98  1.00  0.97  0.93   
Mining                                              0.95  1.01  1.10  1.08   
Utilities                                           0.55  0.52  0.77  0.53   
Construction                                        0.24  0.24  0.24  0.22   
Manufacturing                                       0.44  0.47  0.52  0.49   
Wholesale trade                                     0.18  0.18  0.20  0.19   
Retail trade                                        0.21  0.24  0.24  0.23   
Transportation and warehousing                      0.61  0.59  0.67  0.62   
Information                                         0.21  0.24  0.24  0.25   
Finance and insurance                               0.07  0.11 -0.03 -0.09   
Real estate and rental and leasing                  3.58  2.69  2.83  2.68   
Professional scientific\nand technical services     0.02  0.04  0.03  0.03   
Administrative and support and waste management...  0.09  0.13  0.11  0.12   
Educational services                                0.25  0.27  0.28  0.28   
Health care and social assistance                   0.15  0.17  0.13  0.14   
Arts, entertainment, and recreation                 0.25  0.29  0.21  0.22   
Accommodation and food services                     0.62  0.70  0.64  0.58   
Other services                                      0.33  0.37  0.34  0.32   

                                                    2011  2012  2013  
All                                                 0.32  0.28  0.29  
Agriculture, forestry, fishing, and hunting         0.79  0.67  0.70  
Mining                                              1.03  0.97  1.00  
Utilities                                           0.63  0.77  0.65  
Construction                                        0.21  0.16  0.15  
Manufacturing                                       0.48  0.45  0.46  
Wholesale trade                                     0.19  0.18  0.19  
Retail trade                                        0.23  0.22  0.22  
Transportation and warehousing                      0.61  0.58  0.60  
Information                                         0.24  0.18  0.13  
Finance and insurance                              -0.24 -0.54 -0.58  
Real estate and rental and leasing                  2.82  2.30  2.22  
Professional scientific\nand technical services     0.04  0.01  0.03  
Administrative and support and waste management...  0.11  0.08  0.07  
Educational services                                0.29  0.26  0.27  
Health care and social assistance                   0.15  0.13  0.13  
Arts, entertainment, and recreation                 0.20  0.16  0.14  
Accommodation and food services                     0.56  0.53  0.54  
Other services                                      0.35  0.31  0.33

##  Sales divided by Market Cap (Compustat)
$$ \frac{\text{ sales (COMPUSTAT)  }} {\text{market cap (COMPUSTAT)}  }   $$

In [20]:

display(1/pd.DataFrame(MktCapToSales.iloc[:,0].values,index=MktCapToSales.index,columns=['Avg: 1994-2018'])) 


Avg: 1994-2018
All                                                           0.77
Agriculture, forestry, fishing, and hunting                   0.84
Mining                                                        0.59
Utilities                                                     1.69
Construction                                                  1.88
Manufacturing                                                 0.63
Wholesale trade                                               3.66
Retail trade                                                  1.45
Transportation and warehousing                                1.45
Information                                                   0.44
Finance and insurance                                         0.60
Real estate and rental and leasing                            0.37
Professional scientific\nand technical services               0.70
Administrative and support and waste management...            0.90
Educational services                                          0.55
Health care and social assistance                             1.35
Arts, entertainment, and recreation                           0.77
Accommodation and food services                               0.68
Other services                                                1.00

## Intangible Intensity 
Define $$ii = 1-\frac{K}{V} =1- \frac{K}{S} \times \frac{S}{V}  $$
where 
$$ \frac{K}{S} =  \frac{ \text{TotalTangibleAssets (SOI)  }  } {\text{Business Receipts (SOI) } } $$
and
$$ \frac{S}{V} =  \frac{\text{ sales (COMPUSTAT)  }} {\text{market cap (COMPUSTAT)}  }  $$


In [21]:

display(IITaxdata)

2007  2008  2009  2010  \
All                                                 0.75  0.74  0.74  0.75   
Agriculture, forestry, fishing, and hunting         0.18  0.17  0.19  0.22   
Mining                                              0.44  0.41  0.35  0.37   
Utilities                                           0.07  0.12 -0.31  0.11   
Construction                                        0.54  0.55  0.55  0.58   
Manufacturing                                       0.72  0.70  0.67  0.69   
Wholesale trade                                     0.34  0.34  0.27  0.30   
Retail trade                                        0.69  0.65  0.66  0.67   
Transportation and warehousing                      0.12  0.14  0.03  0.10   
Information                                         0.91  0.89  0.89  0.89   
Finance and insurance                               0.96  0.93  1.02  1.06   
Real estate and rental and leasing                 -0.33  0.00 -0.05  0.00   
Professional scientific\nand technical services     0.98  0.97  0.98  0.98   
Administrative and support and waste management...  0.92  0.88  0.90  0.89   
Educational services                                0.86  0.85  0.85  0.85   
Health care and social assistance                   0.80  0.77  0.82  0.81   
Arts, entertainment, and recreation                 0.81  0.78  0.83  0.83   
Accommodation and food services                     0.57  0.52  0.56  0.60   
Other services                                      0.67  0.63  0.66  0.68   

                                                    2011  2012  2013  
All                                                 0.76  0.78  0.78  
Agriculture, forestry, fishing, and hunting         0.34  0.43  0.41  
Mining                                              0.40  0.43  0.41  
Utilities                                          -0.06 -0.31 -0.09  
Construction                                        0.60  0.70  0.72  
Manufacturing                                       0.69  0.72  0.71  
Wholesale trade                                     0.32  0.32  0.30  
Retail trade                                        0.67  0.69  0.68  
Transportation and warehousing                      0.11  0.16  0.13  
Information                                         0.90  0.92  0.94  
Finance and insurance                               1.14  1.32  1.35  
Real estate and rental and leasing                 -0.05  0.15  0.18  
Professional scientific\nand technical services     0.98  0.99  0.98  
Administrative and support and waste management...  0.90  0.93  0.94  
Educational services                                0.84  0.86  0.85  
Health care and social assistance                   0.80  0.83  0.83  
Arts, entertainment, and recreation                 0.84  0.88  0.89  
Accommodation and food services                     0.62  0.64  0.63  
Other services                                      0.65  0.69  0.67

### Intangible Intensity with FoF liquidity adjustment of 75 %

In [22]:
display(IITaxdataAlt )

2007  2008  2009  2010  \
All                                                 0.67  0.65  0.65  0.67   
Agriculture, forestry, fishing, and hunting        -0.10 -0.11 -0.08 -0.04   
Mining                                              0.25  0.21  0.14  0.16   
Utilities                                          -0.25 -0.18 -0.74 -0.19   
Construction                                        0.39  0.40  0.41  0.45   
Manufacturing                                       0.63  0.61  0.56  0.59   
Wholesale trade                                     0.12  0.12  0.03  0.06   
Retail trade                                        0.59  0.53  0.54  0.55   
Transportation and warehousing                     -0.18 -0.15 -0.29 -0.21   
Information                                         0.88  0.86  0.86  0.85   
Finance and insurance                               0.95  0.91  1.02  1.07   
Real estate and rental and leasing                 -0.77 -0.33 -0.40 -0.33   
Professional scientific\nand technical services     0.98  0.96  0.97  0.97   
Administrative and support and waste management...  0.89  0.85  0.86  0.86   
Educational services                                0.82  0.80  0.79  0.80   
Health care and social assistance                   0.73  0.69  0.76  0.75   
Arts, entertainment, and recreation                 0.74  0.70  0.78  0.77   
Accommodation and food services                     0.43  0.36  0.41  0.47   
Other services                                      0.57  0.51  0.55  0.57   

                                                    2011  2012  2013  
All                                                 0.67  0.71  0.71  
Agriculture, forestry, fishing, and hunting         0.12  0.25  0.21  
Mining                                              0.19  0.24  0.22  
Utilities                                          -0.41 -0.74 -0.46  
Construction                                        0.46  0.60  0.62  
Manufacturing                                       0.59  0.62  0.61  
Wholesale trade                                     0.09  0.10  0.07  
Retail trade                                        0.56  0.58  0.57  
Transportation and warehousing                     -0.18 -0.12 -0.17  
Information                                         0.86  0.90  0.92  
Finance and insurance                               1.19  1.43  1.46  
Real estate and rental and leasing                 -0.39 -0.14 -0.10  
Professional scientific\nand technical services     0.97  0.99  0.98  
Administrative and support and waste management...  0.87  0.90  0.92  
Educational services                                0.79  0.81  0.80  
Health care and social assistance                   0.73  0.77  0.77  
Arts, entertainment, and recreation                 0.79  0.84  0.85  
Accommodation and food services                     0.49  0.51  0.50  
Other services                                      0.54  0.59  0.56

## Additional Details for Real estate and rental and leasing
In the SOI tax data, the real estate sector has a lot of liabilities.These are mainly mortgages/loans on the real estate that is used in the business. We compute the intangible intensity after netting out the mortgage liabilities.  

In [23]:
display(IITaxdataMrtg)

2007  2008  2009  2010  \
All                                                 0.83  0.82  0.82  0.83   
Agriculture, forestry, fishing, and hunting         0.37  0.36  0.42  0.42   
Mining                                              0.55  0.51  0.48  0.48   
Utilities                                           0.35  0.39  0.04  0.36   
Construction                                        0.71  0.71  0.72  0.74   
Manufacturing                                       0.78  0.76  0.73  0.75   
Wholesale trade                                     0.48  0.47  0.43  0.43   
Retail trade                                        0.76  0.72  0.73  0.73   
Transportation and warehousing                      0.34  0.33  0.26  0.28   
Information                                         0.98  1.01  0.94  0.94   
Finance and insurance                               1.00  0.98  1.06  1.07   
Real estate and rental and leasing                  0.19  0.60  0.63  0.64   
Professional scientific\nand technical services     1.01  1.00  1.01  1.01   
Administrative and support and waste management...  0.97  0.94  0.96  0.95   
Educational services                                0.91  0.89  0.88  0.88   
Health care and social assistance                   0.92  0.89  0.94  0.93   
Arts, entertainment, and recreation                 1.01  0.98  1.05  1.01   
Accommodation and food services                     0.73  0.69  0.73  0.76   
Other services                                      0.79  0.75  0.78  0.79   

                                                    2011  2012  2013  
All                                                 0.82  0.85  0.84  
Agriculture, forestry, fishing, and hunting         0.51  0.60  0.57  
Mining                                              0.49  0.55  0.53  
Utilities                                           0.17 -0.05  0.12  
Construction                                        0.73  0.82  0.83  
Manufacturing                                       0.75  0.77  0.76  
Wholesale trade                                     0.44  0.46  0.44  
Retail trade                                        0.73  0.75  0.74  
Transportation and warehousing                      0.28  0.33  0.32  
Information                                         0.94  0.97  0.98  
Finance and insurance                               1.12  1.22  1.25  
Real estate and rental and leasing                  0.57  0.68  0.67  
Professional scientific\nand technical services     1.01  1.02  1.01  
Administrative and support and waste management...  0.95  0.98  1.00  
Educational services                                0.87  0.89  0.88  
Health care and social assistance                   0.91  0.95  0.94  
Arts, entertainment, and recreation                 1.01  1.03  1.03  
Accommodation and food services                     0.76  0.78  0.77  
Other services                                      0.76  0.80  0.78